In [3]:
#Template for Simple coding to Understand how to access json file
import pandas as pd
import requests
import json

# Fetch the JSON data from the URL
url = 'URL Link'
response = requests.get(url)
json_data = response.json()

# Convert the JSON data to a pandas DataFrame
df = pd.DataFrame(json_data)
# Display the DataFrame
print(df)

In [32]:
#Access the ASANA and Import the data in json format
import pandas as pd
import requests
import json

ASANA_BASE_TASK_URL = "https://app.asana.com/api/1.0/tasks"
#Access the link for the ASANA: https://app.asana.com/0/1207638669590015/1207638670232784
PROJECT_ID = "1207638669590015" # This is hardcoded for the purpose of this  example, but I would recommend grabbing the ID you want from an additional API call
personal_access_token = "2/1195781365485212/1207621405062976:08cb575f0db7c127e6f3a4457568453b" # Grab this from env variables or secrets where you saved it!

headers = {
   "Authorization": f"Bearer {personal_access_token}"}

url = f"{ASANA_BASE_TASK_URL}?project={PROJECT_ID}"
# This constructed URL should look something like this: https://app.asana.com/api/1.0/tasks?project=1202095602265837


# Make the API Request. Note the .get() function, which corresponds to the HTTP GET method of our request
response = requests.get(url, headers=headers)


# If the status code is 200, it means the request was successful
if response.status_code == 200:
   tasks = response.json()
   print("The Access to the API was successful")
   print(tasks)
   # After this -- you can do whatever you want with the tasks that is useful to you!


# If status code is not 200, print an error message since something went wrong
else:
   print(f"Failed to retrieve tasks. Status code: {response.status_code}")
   

The Access to the API was successful
{'data': [{'gid': '1207638669590020', 'name': 'Scoping', 'resource_type': 'task', 'resource_subtype': 'default_task'}, {'gid': '1207638670232784', 'name': 'E2E Project Management', 'resource_type': 'task', 'resource_subtype': 'default_task'}]}


In [33]:
#Inspect the data
json_data = tasks
json_data

{'data': [{'gid': '1207638669590020',
   'name': 'Scoping',
   'resource_type': 'task',
   'resource_subtype': 'default_task'},
  {'gid': '1207638670232784',
   'name': 'E2E Project Management',
   'resource_type': 'task',
   'resource_subtype': 'default_task'}]}

In [34]:
#The data contains additional keyword namely 'data' in the beginning. Let's first remove it
json_data_cleaned = json_data['data']
json_data_cleaned

[{'gid': '1207638669590020',
  'name': 'Scoping',
  'resource_type': 'task',
  'resource_subtype': 'default_task'},
 {'gid': '1207638670232784',
  'name': 'E2E Project Management',
  'resource_type': 'task',
  'resource_subtype': 'default_task'}]

In [35]:
#Convert the json data into a DataFrame
df = pd.DataFrame(json_data_cleaned)

df

gid                    name resource_type resource_subtype
0  1207638669590020                 Scoping          task     default_task
1  1207638670232784  E2E Project Management          task     default_task

************************************************
### Join the Project Name with Custom Fields ###
************************************************

In [141]:
####Code to Access the Config Fields along with Main ASANA fields#####

#Access the ASANA and Import the data in json format
import pandas as pd
import requests
import json

ASANA_BASE_TASK_URL = "https://app.asana.com/api/1.0/tasks"
#Access the link for the ASANA: https://app.asana.com/0/1207638669590015/1207638670232784
PROJECT_ID = "1207638669590015" # This is hardcoded for the purpose of this  example, but I would recommend grabbing the ID you want from an additional API call
#PROJECT_ID = "1206713753906403"
personal_access_token = "2/1195781365485212/1207621405062976:08cb575f0db7c127e6f3a4457568453b" # Grab this from env variables or secrets where you saved it!

headers = {
   "Authorization": f"Bearer {personal_access_token}"}

url = f"{ASANA_BASE_TASK_URL}?project={PROJECT_ID}&opt_fields=name,custom_fields.name,custom_fields.display_value"
# This constructed URL should look something like this: https://app.asana.com/api/1.0/tasks?project=1202095602265837


# Make the API Request. Note the .get() function, which corresponds to the HTTP GET method of our request
response = requests.get(url, headers=headers)


# If the status code is 200, it means the request was successful
if response.status_code == 200:
   tasks = response.json()
   print("The Access to the API was successful")
   print(tasks)
   # After this -- you can do whatever you want with the tasks that is useful to you!


# If status code is not 200, print an error message since something went wrong
else:
   print(f"Failed to retrieve tasks. Status code: {response.status_code}")
   

The Access to the API was successful
{'data': [{'gid': '1207638669590020', 'custom_fields': [{'gid': '1207638669590025', 'name': 'NWP Product', 'display_value': 'Proton'}], 'name': 'Scoping'}, {'gid': '1207638670232784', 'custom_fields': [{'gid': '1207638669590025', 'name': 'NWP Product', 'display_value': 'Proton, Prime-Times'}], 'name': 'E2E Project Management'}]}


In [142]:
#Inspect the data
json_data = tasks
json_data

#The data contains additional keyword namely 'data' in the beginning. Let's first remove it
json_data_cleaned = json_data['data']
json_data_cleaned

[{'gid': '1207638669590020',
  'custom_fields': [{'gid': '1207638669590025',
    'name': 'NWP Product',
    'display_value': 'Proton'}],
  'name': 'Scoping'},
 {'gid': '1207638670232784',
  'custom_fields': [{'gid': '1207638669590025',
    'name': 'NWP Product',
    'display_value': 'Proton, Prime-Times'}],
  'name': 'E2E Project Management'}]

In [143]:
json_data_normalized = pd.json_normalize(json_data_cleaned, record_path=['custom_fields'])

In [144]:
# Just extract the Custome Field. Flatten the 'custom_fields' columns
json_data_normalized

gid         name        display_value
0  1207638669590025  NWP Product               Proton
1  1207638669590025  NWP Product  Proton, Prime-Times

In [145]:
#Extract Intake Title
intake_title_data = pd.json_normalize(json_data_cleaned)[['name']].rename(columns={'name':'Intake_Title'})

In [146]:
#Combine the Intake Title dataframe and Custom Field dataframe
intake_data = pd.concat([intake_title_data, json_data_normalized], axis=1)

In [147]:
intake_data.head(2)

Intake_Title               gid         name        display_value
0                 Scoping  1207638669590025  NWP Product               Proton
1  E2E Project Management  1207638669590025  NWP Product  Proton, Prime-Times

In [148]:
intake_data.to_csv('/Users/zishan/Documents/asana_intake_csv_file.csv', index=False)

***
### Access of the **NMT Folder** ###
***

In [1]:
####Experiment to collect Network Planning Fields in ASANA#####

#Access the ASANA and Import the data in json format
import pandas as pd
import requests
import json

ASANA_BASE_TASK_URL = "https://app.asana.com/api/1.0/tasks"
#Access the link for the ASANA: https://app.asana.com/0/1207638669590015/1207638670232784
PROJECT_ID = "1207638669590015" # This is hardcoded for the purpose of this  example, but I would recommend grabbing the ID you want from an additional API call
#PROJECT_ID = "1206713753906403"
personal_access_token = "2/1195781365485212/1207621405062976:08cb575f0db7c127e6f3a4457568453b" # Grab this from env variables or secrets where you saved it!

headers = {
   "Authorization": f"Bearer {personal_access_token}"}

url = f"{ASANA_BASE_TASK_URL}?project={PROJECT_ID}&opt_fields=name,custom_fields.name,custom_fields.display_value"
# This constructed URL should look something like this: https://app.asana.com/api/1.0/tasks?project=1202095602265837


# Make the API Request. Note the .get() function, which corresponds to the HTTP GET method of our request
response = requests.get(url, headers=headers)


# If the status code is 200, it means the request was successful
if response.status_code == 200:
   tasks = response.json()
   print("The Access to the API was successful")
   print(tasks)
   # After this -- you can do whatever you want with the tasks that is useful to you!


# If status code is not 200, print an error message since something went wrong
else:
   print(f"Failed to retrieve tasks. Status code: {response.status_code}")
   

The Access to the API was successful
{'data': [{'gid': '1207344433715257', 'custom_fields': [{'gid': '1207008328334398', 'name': 'NMT UT Owner', 'display_value': 'Timothée Cuignet'}, {'gid': '1206982449331430', 'name': 'NMT_Tech_Umbrella_Topics_OP25', 'display_value': 'ST Scheduling'}, {'gid': '1206328848168146', 'name': 'Lead_Tech/Sci_team_OP25', 'display_value': 'ST Tech - MMPO'}, {'gid': '1206854117206259', 'name': 'OP Status - NMT Tech', 'display_value': 'TBD'}, {'gid': '1206328690471503', 'name': 'Requestor Login_OP25', 'display_value': 'saucsing'}, {'gid': '1206372891341696', 'name': 'ATS_Finance_BCT_Validation_OP25', 'display_value': 'BCT Approved'}, {'gid': '1206372666983567', 'name': 'Total_Entitlement_OP25', 'display_value': '46700000'}, {'gid': '1206463549371893', 'name': 'ATS_Business_Umbrella_Topic(s)_OP25', 'display_value': 'MMN Labor Planning, ST Ops Planning & Scheduling'}, {'gid': '1206336634261352', 'name': 'ATS_Safety_criticality_OP25', 'display_value': 'P3 - Not Cri